In [2]:
import sys
import os
import pickle
import pandas as pd
from datetime import datetime
import pytz
tz=pytz.timezone('Asia/Shanghai')
result_dir = "/home/v-zrr19/alibaba/result/evalution"
summary_dir = '/home/v-zrr19/alibaba/result/root_cause_random_walk'
anomaly_detection_metric_dir = '/home/v-zrr19/alibaba/result/spotCurve'
data_path = '/home/v-zrr19/alibaba/data'
time_range_before=24
time_range_after=1

def timestamp_to_date(timestamp):
    # try:
    #     return datetime.fromtimestamp(timestamp,tz).strftime('%m-%d_%H:%M')
    # except:
        return datetime.fromtimestamp((timestamp//1000),tz).strftime('%m-%d_%H:%M')
    # except:
    #     return datetime.fromtimestamp(timestamp//1000).strftime('%m-%d_%H:%M')
def date_to_timestamp(date):
    # try:
    #     return datetime.fromtimestamp(timestamp,tz).strftime('%m-%d_%H:%M')
    # except:
    date_time_obj = datetime.strptime('2019-%s'%(date), '%Y-%m-%d_%H:%M')
    return tz.localize(date_time_obj).timestamp()
def get_anomaly_metric_spot(anomaly_result, anomaly_time_start, anomaly_time_end, time_range1, time_range2):
    result_all = {}
    #print(anomaly_time)
    
    for metric, value in anomaly_result.items():
        time_length1 = time_range1 * 60 * 60 * 1000
        time_length2 = time_range2 * 60 *60 * 1000
        #print(value['timestamp'])
        # anomaly_in = [timestamp for timestamp in value if (timestamp > anomaly_time - time_length)
        #               & (timestamp <= anomaly_time) ]
        anomaly_in = []
        for timestamp in value:
            if (timestamp > anomaly_time_start - time_length1)  & (timestamp <= anomaly_time_end + time_length2):
                anomaly_in.append(timestamp)
        if len(anomaly_in) != 0:
            result_all[metric]=sorted(anomaly_in)         
    return result_all
def get_max_threshold_metric(time_list,threshold_df,data_df):
    max_rate = 0
    for time in time_list:
        try:
            rate = (data_df.loc[data_df['timestamp'] == time].values[0][1]-threshold_df.loc[threshold_df['timestamp'] == time].values[0][1]) /threshold_df.loc[threshold_df['timestamp'] == time].values[0][1]
        except:
            # print('metric',time)
            # print('No threshold (the first day data)')
            continue
        if rate > max_rate:
            max_rate = rate
    print('max_rate_t_m',max_rate)
    return max_rate


def get_max_threshold_metric_success(time_list, threshold_df, data_df):
    max_rate = 0
    for time in time_list:
        try:
            rate = (threshold_df.loc[threshold_df['timestamp'] == time].values[0][1]-
                    data_df.loc[data_df['timestamp'] == time].values[0][1]
                    ) / \
                   threshold_df.loc[threshold_df['timestamp'] == time].values[0][1]
            #print('data', data_df.loc[data_df['timestamp'] == time].values[0][1])
            #print('threshold', threshold_df.loc[threshold_df['timestamp'] == time].values[0][1])

        except:
            # print('success',time)
            # print('No threshold (the first day data)')
            continue
        if rate > max_rate:
            max_rate = rate
    print('max_rate_t_m_s',max_rate)
    return max_rate


In [5]:
if __name__ == '__main__':
    
    
    print('sdddfffkd')

    with open (os.path.join(result_dir,'given_root_result.pickle'),'rb')as fr:
        roots=pickle.load(fr)
    
    for root in roots:
        date=root['date']
        file=root['app']
        df = pd.read_csv(os.path.join(data_path,date,file+'.csv')).drop(columns=['app_name']).dropna(axis='columns',how='all')
        columns = df.drop(columns=['timestamp']).columns.values
         #print(columns)
         #print(type(columns))
        metric_anomaly_file = os.path.join(anomaly_detection_metric_dir, date, file, 'metric',
                                        'anomaly_time.pickle')
        metric_anomaly_threshold_file = os.path.join(anomaly_detection_metric_dir, date,file,
                                                                  'metric', 'threshold.pickle')
        with open(metric_anomaly_file, 'rb') as fr:
            metrics_anomaly_time = pickle.load(fr)
        with open(metric_anomaly_threshold_file, 'rb') as fr:
            metrics_anomaly_threshold = pickle.load(fr)
        rates={}
        kpi=[root['anomaly_time'][0:11],'_',root['anomaly_time'][12:]]
        tmep=''.join(kpi)
        time_date=tmep.split('_')
        time_start=time_date[0]+'_'+time_date[1]
        time_end=time_date[2]+'_'+time_date[3]
        print(date_to_timestamp(time_start))
        print(date_to_timestamp(time_end))
        
        
        #print(metrics_anomaly_time)
        anomaly_metrics = get_anomaly_metric_spot(metrics_anomaly_time, date_to_timestamp(time_start)*1000,
                                                  date_to_timestamp(time_end)*1000,time_range_before,time_range_after)
        #print(anomaly_metrics)
        for column in columns:
            if column=='avg(middleware.metaq.receive.rt)'or column=='avg(web.rt)' or column=='avg(middleware.hsf.provider.rt)'or column=='avg(middleware.notify.receive.rt)':
                continue
            else:
                if column in anomaly_metrics.keys():
                    df_sequence = df[['timestamp', column]].copy()
                    df_sequence.loc[:, column] = df_sequence[column].fillna(df_sequence[column].mean())
                    if column == 'avg(jvm.mem.heap.usage)' or column == 'avg(system.mem.util)' or column.find(
                                'qps') + 1:
                        max_rate1 = get_max_threshold_metric_success(anomaly_metrics[column],
                                                                         metrics_anomaly_threshold[column][
                                                                             'lower'], df_sequence)
                        max_rate2 = get_max_threshold_metric(anomaly_metrics[column],
                                                                 metrics_anomaly_threshold[column]['upper'],
                                                                 df_sequence)
                        max_rate = max(max_rate1, max_rate2)
                    else:
                        if column.find('rate') + 1:
                            max_rate = get_max_threshold_metric_success(anomaly_metrics[column],
                                                                            metrics_anomaly_threshold[column][
                                                                                'lower'], df_sequence)
                        else:
                            max_rate = get_max_threshold_metric(anomaly_metrics[column],
                                                                    metrics_anomaly_threshold[column]['upper'],
                                                                            df_sequence)
                else:
                    max_rate=0.000000
                    
            rates[column]=max_rate 
            print(rates)
            
        #rates=sorted(rates.items(), key=lambda item:item[1],reverse=True)
    
        max_rates=pd.DataFrame({'metrics':list(rates.keys()),'max_rate':list(rates.values())})
        print(max_rates)
        print(max_rates['max_rate'].sum())
        save_max_rate_path=os.path.join(result_dir,'rate',date,file)
        if not os.path.exists(save_max_rate_path):
            os.makedirs(save_max_rate_path)
        with open (os.path.join(save_max_rate_path,root['kpi']+'_'+tmep+'.pickle'),'wb') as fw:
            pickle.dump(max_rates,fw)
        

sdddfffkd
1569057480.0
1569057600.0
max_rate_t_m 10.344822100079593
{'avg(system.cpu.util)': 10.344822100079593}
{'avg(system.cpu.util)': 10.344822100079593, 'avg(system.cpu.steal)': 0.0}
max_rate_t_m 17.71782949942587
{'avg(system.cpu.util)': 10.344822100079593, 'avg(system.cpu.steal)': 0.0, 'avg(system.load.load1.util)': 17.71782949942587}
max_rate_t_m 7.184976704204196
{'avg(system.cpu.util)': 10.344822100079593, 'avg(system.cpu.steal)': 0.0, 'avg(system.load.load1.util)': 17.71782949942587, 'avg(system.load.load5.util)': 7.184976704204196}
max_rate_t_m 2.9311404393931193
{'avg(system.cpu.util)': 10.344822100079593, 'avg(system.cpu.steal)': 0.0, 'avg(system.load.load1.util)': 17.71782949942587, 'avg(system.load.load5.util)': 7.184976704204196, 'avg(system.load.load15.util)': 2.9311404393931193}
max_rate_t_m 15.128408016840723
{'avg(system.cpu.util)': 10.344822100079593, 'avg(system.cpu.steal)': 0.0, 'avg(system.load.load1.util)': 17.71782949942587, 'avg(system.load.load5.util)': 7.1